## Brief introduction

`polymake` is open source software for research in polyhedral geometry and other areas of mathematics. It deals with polytopes, polyhedra and fans as well as simplicial complexes, matroids, graphs, tropical hypersurfaces, and other objects. 

Supported platforms include various flavors of Linux, FreeBSD and Mac OS.

To get a copy of polymake, installation procedure, user guide and documentation and other information, please visit [polymake wiki](https://polymake.org/doku.php/start)

To use polymake directly in Oscar, enter $ after calling Oscar in julia. 

To use polymake with jupyter notebook, run in polymake:

polymake --script jupyte

To navigate to a different application within polymake, use for example:

In [111]:
application "polytope";

The difference between the current application and the rest is that you can call the functions and object constructors of the former without having to qualify them with the application name as a prefix. To call functions from other applications, for example from the application "ideal", do the following for instance:

In [112]:
$I = ideal::pluecker_ideal(3,6);

For getting help about a particular function during a polymake session, use for example:

In [107]:
help "Polytope";

polytope/objects/Polytope:
 Not necessarily bounded convex polyhedron, i.e., the feasible region of a linear program.
 Nonetheless, the name "Polytope" is used for two reasons: Firstly, as far as the combinatorics
 is concerned we always deal with polytopes; see the description of VERTICES_IN_FACETS for details.
 Note that a pointed polyhedron is projectively equivalent to a polytope.
 The second reason is historical.
 We use homogeneous coordinates, which is why Polytope is derived from Cone.

Type Parameters:
  Scalar numeric data type used for the coordinates, must be an ordered field. Default is Rational.

Examples:

*) To construct a polytope as the convex hull of three points in the plane use
   > $p=new Polytope(POINTS=>[[1,0,0],[1,1,0],[1,0,1]]);
   > print $p->N_FACETS
     3
    Note that homogeneous coordinates are used throughout.
*) Many standard constructions are available directly.  For instance, to get a regular 120-cell (which is 4-dimensional) use:
   > $c=regular_120

## General tutorial on polytopes and interactions with other objects


### Constructing a polytope from scratch

To define a polytope as the convex hull of finitely many points, you can pass a matrix of coordinates to the constructor. Since `polymake` uses [homogeneous coordinates](coordinates.ipynb), you need to set the additional coordinate x<sub>0</sub> to 1.

In [84]:
$m = new Matrix([[1,1,0,0],[1,-1,0,0],[1,0,1,0],[1,0,-1,0],[1,0,0,1],[1,0,0,-1]]);

In [85]:
$p1 = new Polytope(POINTS=>$m);

In [30]:
$p1->VISUAL;

<!--
polymake for balla
Wed Jan 31 11:45:42 2024
p
-->


 
 
 
 p 
 
 
 
 
 
 
 Transparency 
 
 depthWrite 
 
 
 
 Rotation 
 
 x-axis 
 y-axis 
 z-axis 
 Reset 
 

 Rotation speed 
 
 


 
 Display 
 
 
 
 Objects 
 
 
 
 
 
 
 Camera 
 
 
 
 Perspective 
 Orthographic 
 
 
 
 

 
 SVG 
 
 
 Download 
 New tab 
 
 Screenshot 
 
 

 <!-- end of settings -->

We can also create polytopes from the H-description, for example:

In [86]:
$p2 = new Polytope(INEQUALITIES=>[[1,1,0],[1,0,1],[1,-1,0],[1,0,-1],[17,1,1]]);

### Computing properties of objects

Several propeties of the objects created can be computed with a single command. Here are a few examples:

In [109]:
print $p1->VERTICES;

1 1 0 0
1 -1 0 0
1 0 1 0
1 0 -1 0
1 0 0 1
1 0 0 -1


In [88]:
print $p1->N_FACETS;

8

In [89]:
print $p1->VERTICES_IN_FACETS;

{1 2 4}
{1 3 4}
{1 3 5}
{1 2 5}
{0 2 5}
{0 2 4}
{0 3 4}
{0 3 5}


In [90]:
print  $p1->F_VECTOR;

6 12 8

In [91]:
print_constraints($p2->INEQUALITIES);

0: x1 >= -1
1: x2 >= -1
2: -x1 >= -1
3: -x2 >= -1
4: x1 + x2 >= -17
5: 0 >= -1



In [103]:
$S = new fan::SubdivisionOfPoints(POINTS=>$p1->VERTICES,WEIGHTS=>[1,2,0,-1,0,1]);

In [104]:
print $S->MAXIMAL_CELLS;

{1 2 3 5}
{1 2 3 4}
{0 2 3 5}
{0 2 3 4}


In [105]:
$S->VISUAL;

<!--
polymake for balla
Thu Feb 1 08:12:48 2024
pcom:S
-->


 
 
 
 pcom:S 
 
 
 
 
 
 
 Explode 
 
 Automatic explosion 
 Exploding speed 
 
 
	
 
 Transparency 
 
 depthWrite 
 
 
 
 Rotation 
 
 x-axis 
 y-axis 
 z-axis 
 Reset 
 

 Rotation speed 
 
 


 
 Display 
 
 
 
 Objects 
 
 
 
 
 
 
 Camera 
 
 
 
 Perspective 
 Orthographic 
 
 
 
 

 
 SVG 
 
 
 Download 
 New tab 
 
 Screenshot 
 
 

 <!-- end of settings -->

### Rule Based Computation

New properties are derived from known ones via rules. The status of an object is described via the set of properties known. Asking for a new property forces polymake to compute a sequence of rules (forming a schedule) which is then applied to the object. Usually, this is automatic. However, it is possible to inspect what is going on before any actual computation takes place.

In [106]:
print join(", ", $p1->list_properties);

POINTS, CONE_AMBIENT_DIM, FEASIBLE, N_POINTS, CONE_DIM, FULL_DIM, BOUNDED, POINTED, LINEALITY_DIM, LINEALITY_SPACE, COMBINATORIAL_DIM, AFFINE_HULL, FACETS, VERTICES_IN_FACETS, VERTICES, N_FACETS, N_VERTICES, F_VECTOR

In [82]:
$schedule=$p1->get_schedule("SIMPLE");

In [121]:
print join("\n", $schedule->list);

SIMPLE : COMBINATORIAL_DIM, RAYS_IN_FACETS

In [122]:
$schedule->apply($p1);

In [123]:
print $p1->SIMPLE;

false

### Saving and loading data

You can save and load data obtained from a particular object, and this can be loaded in polymake. For example, we can save the data obtained on the object $p1 and then load it.

In [126]:
save($p1,"myPolyObject.poly");

In [127]:
$k=load("myPolyObject.poly");

In [131]:
print $k->F_VECTOR;

6 12 8

### Interaction with `polymake`

Please click on any of the following links to try out other things. These are introductory tutorials for the applications on the different mathematical topics you can use polymake for (found in the user guide from polymake wiki).

[fan](https://polymake.org/doku.php/user_guide/tutorials/apps_fan) for fans

[fulton](https://polymake.org/doku.php/user_guide/tutorials/apps_fulton) for toric varieties

[graph](https://polymake.org/doku.php/user_guide/tutorials/apps_graph) for graphs

[group](https://polymake.org/doku.php/user_guide/tutorials/apps_group) for groups and their actions on polymake objects

[matroid](https://polymake.org/doku.php/user_guide/tutorials/apps_matroid) for matroids

[polytope](https://polymake.org/doku.php/user_guide/tutorials/apps_polytope) for polyhedra

[topaz](https://polymake.org/doku.php/user_guide/tutorials/apps_topaz) for topology

[tropical](https://polymake.org/doku.php/user_guide/tutorials/apps_tropical) for tropical geometry
